In [2]:
import requests
from bs4 import BeautifulSoup
import re
import pandas as pd
import os 
import ast
import json
import time
from requests.exceptions import ConnectionError

https://stackoverflow.com/questions/62335537/scraping-text-from-kickstarter-projects-return-nothing

In [3]:
base = "/Users/ivankoh/Downloads/kickstarter data/"
filepaths = [base + f for f in os.listdir(base) if f.endswith('.csv')]
df = pd.concat(map(pd.read_csv, filepaths))
df_1 = df.drop_duplicates(subset=['id'])
df_1['main_url'] = df_1['urls'].apply(lambda x: eval(x)['web']['project'])
print(len(df))
print(len(df_1))

392244
203510


/var/folders/dq/33rpc0cx4f54t0vx2cdcgczr0000gn/T/ipykernel_1591/4110031066.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_1['main_url'] = df_1['urls'].apply(lambda x: eval(x)['web']['project'])


In [4]:
def get_slug(url):
    return re.search('/projects/(.*)\?', url).group(1)

# get the slug from the urls. the slug is the input to the GraphQL API call 
slugs = list(map(get_slug, df_1['main_url'].tolist()))
# while iterating through all projects, add the story and risk to these lists. At the end len of both list 
# should be the same as the len of the dataframe. if all good then add as columns to the dataframe df. 
story_list2 = []
risk_list2 = []

In [ ]:
# instantiate a new Session 
s = requests.Session()

query = """
query Campaign($slug: String!) {
  project(slug: $slug) {
    risks
    story(assetWidth: 680)
  }
}"""

# PARAMS
counter = 0
block_number = 0
agents = [
         "Mozilla/5.0 (Symbian/3; Series60/5.2 NokiaN8-00/012.002; Profile/MIDP-2.1 Configuration/CLDC-1.1 ) AppleWebKit/533.4 (KHTML, like Gecko) NokiaBrowser/7.3.0 Mobile Safari/533.4 3gpp-gba",
         "Mozilla/5.0 (Linux; Android 5.0; Lenovo S60-a Build/LRX21T) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/56.0.2924.87 YaBrowser/17.3.1.383.00 Mobile Safari/E7FBAF",
         "Mozilla/5.0 (iPhone; CPU iPhone OS 15_5 like Mac OS X) AppleWebKit/605.1.15 (KHTML, like Gecko) Mobile/15E148 Instagram 244.0.0.12.112 (iPhone12,1; iOS 15_5; en_US; en-US; scale=2.00; 828x1792; 383361019)",
         "Mozilla/5.0 (Linux; U; Android 2.2.1; en-US; GT-S5830 Build/FROYO) AppleWebKit/534.31 (KHTML, like Gecko) UCBrowser/9.0.1.275 U3/0.8.0 Mobile Safari/534.31",
         "Mozilla/5.0 (Linux; Android 11; Redmi Note 8 Pro) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/104.0.0.0 Mobile Safari/537.36"
         ]

# pause for 30 seconds every 5 iterations
for i in range(63830, 81405):
    slug = slugs[i]
    if counter == 5:
        print("TAKING A NAP ZZZ...")
        time.sleep(30)
        counter = 0
    counter += 1
    print(f"--------{slug}------")
    # POST request to GraphQL API situated in kickstarter domain 
    # response from POST request should contain the story and risks
    connect_try = 0
    not_found = True
    while connect_try < 30 and not_found:       
        try:
            r = s.post("https://www.kickstarter.com/graph",
                headers = {
                  'content-type': 'application/json',
                  'x-csrf-token': 'bL5nMRm5s147N8RxvNcth-E8NAOt3SprGYtvvKsVLnuZ3XwQ71cy1zrDfjIAGTCHV0obMRNqRMbBJT7nF2ZSAA',
                  'User-Agent': 'Mozilla/5.0 (Windows NT 6.1; WOW64; rv:50.0) Gecko/20100101 Firefox/50.0',
                  'cookie': '_ksr_session=eus10UNK7iB%2FwIMXafXg5yJdYvRD7rHlR%2Ba1KEbUnB5EKTgQxNKEIqrp%2BIyjRC%2FNXw76u4Eki4AsiBom5M1LKNJKWCD65CBzeegWrk2%2FRV9Sht6dlOKplCATNdrmEIIa0Bt%2FKKGnT2m9ID1nTCduj73%2BdeJK663MNcbYWXBHkFyZJgUKh4JcCx3hL0UF2quVeBvfV45M0CNrT1j4DchvTlFBn%2BpE37ZaGldNz7BF0RAcCjIZrt%2FzNkxugCaFfWEPjxh9amOCvytIcdjxOaE68AAmHuU%3D--RPNmoWC%2FGnWTmsfw--9466UG%2Bqs2V%2F8B8zFtXUig%3D%3D'
                },
                json = {
                    "operationName":"Campaign",
                    "variables":{
                        "slug": slug
                    },
                    "query": query
                })
            not_found = False
        except ConnectionError:
            print("Connection Error")
            time.sleep(5)
            connect_try += 1
    try:
        result = r.json()
        print("-------STORY--------")
        story_html = result["data"]["project"]["story"]
        soup = BeautifulSoup(story_html, 'html.parser')
        curr_story = []
        for i in soup.find_all('p'):
            print(i.get_text())
            curr_story.append(i.get_text())
        story_list2.append(" ".join(curr_story) if curr_story else "")

        print("-------RISKS--------")
        print(result["data"]["project"]["risks"])
        risk_list2.append(result["data"]["project"]["risks"] if result["data"]["project"]["risks"] else "")
    except:
        print(r)
        story_list2.append("")
        risk_list2.append("")
        continue

--------905031711/trago-the-worlds-first-smart-water-bottle------
-------STORY--------
With all of the tools out there to track and improve performance, why aren’t we paying closer attention to measuring hydration - one of the most important driving factors of health and athletic performance? Water is the most abundant element in our body – it makes up 70% of our muscles, lubricates our joints, and delivers nutrients to our body. However, most of us don’t know how much water we drink every day and, more importantly, how much we should drink. 
Trago is a patent-pending water bottle that accurately measures how much you drink. It connects to your smart phone, and other wearable devices, and allows you to set, and measure, intelligent hydration goals. Optimal hydration is both art and science, and it’s different for everyone. Trago helps you pinpoint the perfect amount for you.
Trago's vision is to change the way people think about hydration. #hydratesmarter 
How much should you drink? Hy

-------STORY--------
I am a school social worker, and I am working in a rural community that craves connection and meaningful human experiences.  Our school district is amazing, and our community desires the opportunity to exhibit pride... however there are minimal options in regards to spirt wear... business pride... and frankly connection via wearing the brand of our community.  I have lived in a community that invested in an embroidery shop that created personalized and customized apparel for the village, and I have seen pride in the community, and the culture of the community increased ten fold.  I am looking to achieve the same goal here.  Strong community culture, strong small town pride, Strong ties/shareholding to investing in the community!  
-------RISKS--------
The great news is... there is only 1 other embroidery business with a 25 mile distance from the heart of the community... and they specialize in screen printing vs. threaded embroidery!
--------118216821/awareness-pro

-------STORY--------
6 Kickstarter treffen sich einen ganzen Samstag hier bei uns im Schulungszentrum in Ober-Mörlen und sind dabei, wenn wir einen 6 Stunden Video-Kurs für alle produzieren die nicht live dabei sein können oder wollen. 
Und da alle Kickstarter einfach klasse Typen sind, werden die sechs Vor-Ort-Teilnehmer nach den Dreharbeiten bei einem Barbecue mit den Dozenten zusammen sitzen und den Tag mit Grillgut und verschiedenen Getränken ausklingen lassen. Die einzige Bedingung dabei ist es, zu Fachsimpeln und mögliche Projekte zu besprechen, bis der Arzt kommt :-)
Bis zu 30 Kickstarter sind am selben Tag als Webinargäste live dabei, können auch Fragen stellen und haben gleich im Anschluss Zugriff auf alle Beispiele, Projekte und Quelltexte des Tages.
Beliebig viele Kickstarter sichern sich die Videos und alle Downloads des Projekttages, wobei die Videos erst drei Wochen nach der Veranstaltung zur Verfügung stehen.
Unser Seminartag beginnt Samstag, den 20. Juni 2015, anreisefr

-------STORY--------
With use of unique rewards Jason is creating a fun and exciting way for you to help fund his new music album release "Nothing's Forever". The music stemming from the worlds curveballs during the last 4 years of his life. This album will keep you guessing to what is next. The vibe is funky, reflective and emotional while keeping concentrated and precise. From start to finish "Nothing's Forever" tells the 4th chapter of Jason's life through music. High production work while keeping true to his roots of creating fun, upbeat and thought-provoking music.
This massive 16 track album features 3 remixes of "Another Day", "Gamers Alike" and "I Don't Know" with cover artwork produced by "DODOFRO"! Guitar work from Mike Turner, Bass guitar by Jon Heake & Jarrod Karnofski and a song collaboration with Stiv-One (Let Cha Know)!
Please take a listen, check out the rewards, and pitch in if you would like!
"Thanks to all the JH music supporters over the years, old and new I owe thi

-------STORY--------
At SwitchDoc Labs, we build a lot of cool projects.  Sometimes they become products, other times they are customer funded or proof-of-concept projects.  MouseAir (named one of the 15 most creative Raspberry Pi Projects by Brit+CO), Project Curacao, SunTracker, SunAirPlus and the new Solar Powered Semi-autonomous robot SunRover are all part of the project flow around here.  We often write articles about these projects that lands us on magazine covers.  This Kickstarter is to take to production two boards that we find really, really useful.  Check out our other products and useful blogs at www.switchdoc.com.
Board 2:  Quad Power Management I2C Board - Switch on and off batteries, power supplies and solar panels
features:
Full descriptions of these boards are below.
The I2C 8 GPIO Extender board is fully tested will be released to production within the next two weeks.   The Quad Power Management Board has just arrived in prototypes and we will start testing all the fe

...

-------STORY--------
HELLO HUMANS!!!
My name is Holly and I am the person behind @Lazycreative_
Here is my series of Harry Potter quote pins, which is new to kickstarter. Hopefully with you guys, we can get these made and sent out by the beginning of December so they are in their new homes in time for Christmas presents!!! (Yes it's not even Halloween yet and I'm talking about Christmas already!)
I am a huge Potterhead and since starting Lazy Creative I have wanted to join the Wizarding game. so this is my second wizarding pins series!!! I hope that these pins are different as that is what i wanted to do. I wanted to create a series of quote pins that haven't been seen or not seen much in the enamel pin world and I feel I have accomplished this!
I hope that you guys love them and we can unlock as many pins as we can, I have also Listed all of the pins below in the mockup of what they will roughly look like when they have been produced and popped on their new backing cards with the meta

-------STORY--------
A Gripping Tale of success over severe adversity in the world of Commodore and Amiga
Commodore and Amiga fans we are pleased to announce the exciting new book from David John Pleasance and Trevor Dickinson 
Hello and welcome to my new Kickstarter for the book that is going to tell it all!
Starting from the day when Escom were the highest bidder at Commodore's  liquidator’s auction in New York (I was there), how their attempts to relaunch the Amiga spectacularly failed, then the troublesome years when our beloved computer bounced around from company to company, Viscorp, Quickpack, Gateway 2000, etc. and beyond.
This book leaves no stone unturned in revealing how the Commodore-Amiga assets became the target of a multiple of companies and individuals, some of whom were seemingly only interested in what they could gain out of it financially, and not even interested in supporting any of the many devotees who were trying to keep the dream alive.
In fact there was so much

-------STORY--------
Si quieres leer en español haz click aquí
BACKGROUND
Benjamín was born in 2001 in Ambato, Ecuador. A year after his birth his mother and father brought him to Barcelona, travelling over 9,000km in a desperate search for the answers that doctors in Ecuador could not provide. Their son had been born with severe malformations to his upper and lower limbs due to the effects of Thalidomide, a drug that Benjamín's mother had been prescribed during pregnancy to ease her morning sickness. And she was not a unique case. As a matter of fact, Thalidomide was recommended and sold to pregnant women worldwide during the late 50s and early 60s. Lavish marketing campaigns assured that the drug was 100 percent safe and ‘worked wonders’ to help combat morning sickness. Thalidomide was banned in many countries in the 60s, nevertheless Benjamin's mother took it in Ecuador in the year 2000.
Thalidomide is now known as one of the biggest tragedies in modern time medicine. In Europe alon

-------STORY--------
Beldame comes from the roots belle (beautiful) and dame (woman), but the definition is “old woman,” or “hag,” especially connoting evil or witchcraft. It’s a paradox familiar to the experience of womanhood, to be put on a pedestal in one breath and vilified in the next. “Beldame” captures the feeling of existing in both aspects, maiden and crone, loved and reviled.
I’m Lulu Black, violinist, vocalist, composer and songwriter. Beldame began as an off-shoot of my self-titled solo project, which then became a collaboration with producer, composer, and guitarist Mike Hart.
We were nearing completion of our first 7-track LP when COVID hit and the music industry shut down. But despite that, we have continued to write, record and mix remotely to get this album finished. We’re incredibly proud of what we’re making and can’t wait to share it with the world.
This album, which we’re calling “Unrequited” is fueled by themes of loss, love, grief, and the supernatural. Woman as 

-------STORY--------
Hey there friends from old and new! Come pledge $20 ($15 LP & $5 US shipping costs) to help us release our new album on vinyl! If you pledge, you will receive our new LP 'To Hell with the Smiles' when/if our goal is met! Side A will feature 5 brand new songs. Side B will feature our 2016, 5 song EP ’Death Ride’. 10 songs total, making one full-length 12" LP on wax! We were well on our way to funding this project ourselves, but after recording, mastering, artwork, and the fact that we have been unable to play live music since February, we have fallen a little short. That's where we need your help. We have a small goal of $1000 to reach. We are an un-signed band, with zero label support, so we are 100% releasing this album ourselves. This will work like a pre-order, and if our goal is not made, we keep nothing, and you keep your pledge. We just need your help to make this happen! The new LP will feature cover artwork by OKC artist Matt Schneider, it comes with a full

# Saving Data

## Latest Iteration Ran Till: 63829, Local copy latest: 44135_63829



In [39]:
#SAVE LIST IN LOCAL FOR USE LATER. NAME FILE AS {from}_{to]_{story/risk}.json
story_file_name = "/Users/ivankoh/Downloads/bt4222 data/44135_63829_story" #CHANGE THIS
risk_file_name = "/Users/ivankoh/Downloads/bt4222 data/44135_63829_risk" #CHANGE THIS 

story_file_name += ".json"
risk_file_name += ".json"

with open(story_file_name, 'w') as f:
    # indent=2 is not needed but makes the file human-readable 
    # if the data is nested
    json.dump(story_list2, f, indent=2) 

with open(risk_file_name, 'w') as f:
    # indent=2 is not needed but makes the file human-readable 
    # if the data is nested
    json.dump(risk_list2, f, indent=2) 
    
# with open(story_file_name, 'r') as f:
#     story_subset = json.load(f)

In [41]:
print("risk:", len(risk_list2),"\n", "story:", len(story_list2))
44135 + 19695  



risk: 19695 
 story: 19695


63830

In [16]:
with open('/Users/ivankoh/Downloads/bt4222 data/44135_48799_risk.json', 'r') as f:
    risk_subset = json.load(f)

In [17]:
len(risk_subset)

4665

In [34]:
print("LATEST CALL DF ROW", "\n")
print(df_1.iloc[63515-1]['blurb'])

print("LATEST STORY IN LIST", "\n")
print(story_list2[-1])

print("LATEST RISK IN LIST", "\n")
print(risk_list2[-1])

LATEST CALL DF ROW 

A collection of worship songs for the church to sing. Songs born during a three year period in which we saw God heal our son of cancer.
LATEST STORY IN LIST 

I have the honor of serving as the Worship Pastor of Messiah's House Church in Amarillo, TX.  My heart is to write songs for the church to sing.  Through music, I hope to help give people language to express their hearts to God in worship. My wife and I experienced a season of difficulty when our son, Reeve, was diagnosed with Leukemia in October of 2017 just days before his 2nd birthday.  By the grace of God, Reeve is in remission and cancer-free! During that season, I've written songs of that I believe will help others on their journey.  I'm asking you to help me raise $10,000 towards this project.  It would mean the world to me if you were able to help me accomplish my dream of recording my first full-length album! To see a list of where your money will go, see below: Costs include:
LATEST RISK IN LIST 

K

In [165]:
s = requests.Session()

In [434]:
import requests
import json

url = "https://www.kickstarter.com/graph"

payload = json.dumps([
  {
    "operationName": "Campaign",
    "variables": {
      "slug": "leightonconnor/akashic-titan-blue-bolt"
    },
    "query": "query Campaign($slug: String!) {\n  project(slug: $slug) {\n    id\n    isSharingProjectBudget\n    risks\n    story(assetWidth: 680)\n    currency\n    spreadsheet {\n      displayMode\n      public\n      url\n      data {\n        name\n        value\n        phase\n        rowNum\n        __typename\n      }\n      dataLastUpdatedAt\n      __typename\n    }\n    environmentalCommitments {\n      id\n      commitmentCategory\n      description\n      __typename\n    }\n    __typename\n  }\n}\n"
  }
])
headers = {
  'content-type': 'application/json',
  'x-csrf-token': 'bL5nMRm5s147N8RxvNcth-E8NAOt3SprGYtvvKsVLnuZ3XwQ71cy1zrDfjIAGTCHV0obMRNqRMbBJT7nF2ZSAA',
  'User-Agent': 'Mozilla/5.0 (Windows NT 6.1; WOW64; rv:50.0) Gecko/20100101 Firefox/50.0',
  'cookie': '_ksr_session=eus10UNK7iB%2FwIMXafXg5yJdYvRD7rHlR%2Ba1KEbUnB5EKTgQxNKEIqrp%2BIyjRC%2FNXw76u4Eki4AsiBom5M1LKNJKWCD65CBzeegWrk2%2FRV9Sht6dlOKplCATNdrmEIIa0Bt%2FKKGnT2m9ID1nTCduj73%2BdeJK663MNcbYWXBHkFyZJgUKh4JcCx3hL0UF2quVeBvfV45M0CNrT1j4DchvTlFBn%2BpE37ZaGldNz7BF0RAcCjIZrt%2FzNkxugCaFfWEPjxh9amOCvytIcdjxOaE68AAmHuU%3D--RPNmoWC%2FGnWTmsfw--9466UG%2Bqs2V%2F8B8zFtXUig%3D%3D'
}

response = requests.request("POST", url, headers=headers, data=payload)
print(response.status_code)
print(response.json()[0]['data']['project']['risks'])

200
This is my fourth solo Kickstarter campaign, and I delivered all three of my previous games in a timely manner. 

I have a complete draft of the text, with the exception of Appendix 1. I have a team of editors lined up who will give me feedback so that I can revise, expand, and polish it as needed. The most time-consuming tasks will be completing the artwork and the layout. I've done this before, with the previous Akashic Titan zine and with my game Project 8Ball. Depending on the stretch goals I will be depending on someone else for illustrations and additional text, but I have worked with Josh before and I am confident he will hit his deadlines. 

I believe I will be able to finish the book by June, but just to be cautious I have set the estimated delivery month as July. 

Barring any unforeseen catastrophes, I should have no problem printing and shipping the zine by July.


In [435]:
import requests
import json

url = "https://www.kickstarter.com/graph"

payload = json.dumps([
  {
    "operationName": "Campaign",
    "variables": {
      "slug": slugs[4290]
    },
    "query": "query Campaign($slug: String!) {\n  project(slug: $slug) {\n    id\n    isSharingProjectBudget\n    risks\n    story(assetWidth: 680)\n    currency\n    spreadsheet {\n      displayMode\n      public\n      url\n      data {\n        name\n        value\n        phase\n        rowNum\n        __typename\n      }\n      dataLastUpdatedAt\n      __typename\n    }\n    environmentalCommitments {\n      id\n      commitmentCategory\n      description\n      __typename\n    }\n    __typename\n  }\n}\n"
  }
])
headers = {
  'content-type': 'application/json',
  'x-csrf-token': 'fvjxrhwSYir6BG4U761oTRMXCYu4Ql88J4gTJaaXswCLm-qP6vzjo_vw1FdTY3VNpWEmuQb1MZH_JkJ-GuTPew',
  'user-agent': 'Mozilla/5.0 (Linux; U; Android 2.3.4; en-us; Kindle Fire Build/GINGERBREAD) AppleWebKit/533.1 (KHTML, like Gecko) Version/4.0 Mobile Safari/533.1',
  'cookie': '_ksr_session=XeMoOdlfAuvBg3vZkCPtR2KPkjnWtoE%2FGrwY68dNgE13OYvjkIxO0Eiaf4Oay2xzILiIHuLsmpCAH%2B9aBGT01%2B7gNDH6exw0dtPhWF5xVSYtZnJawqJNc8IUuF52GC%2FS7QHp1woosgy6PABnOt0X0ITzAvUEg8wwMmv5e1IBYNCmj8ZiCiUwlU2h08X3WX0lQSBSeatHjTEHV%2FgAjhqitXq1xvrNIY7MvvonoTMQat4mSbJKrOzGi74PUMwlhlgHz1oDCWy%2BqAiY%2BIQp9ft4c%2BK2ta8%3D--Rds4wbR2FagzmGoy--ZV4JbIYN8J%2FdS8uWWa5EQw%3D%3D'
}

response = requests.request("POST", url, headers=headers, data=payload)
print(response.status_code)
print(response.json()[0]['data']['project']['risks'])

200
Spectrum South’s risk is minimal as we have a comprehensive operating plan to continue, as well as expand our current work. We have a proposed budget based off of the funding received from this Kickstarter which we can execute immediately.

If you have any questions regarding this project, feel free to email us at info@spectrumsouth.com.


In [255]:
s = requests.Session()
headers = {
            'content-type': 'application/json',
            'User-Agent': 'Mozilla/5.0 (Windows NT 6.1; WOW64; rv:50.0) Gecko/20100101 Firefox/50.0',
          }
# GET request to kickstarter to get some token needed for later 
r = s.get("https://www.kickstarter.com", headers=headers)
#BeautifulSoup parses the html returned as a response from the GET request 
soup = BeautifulSoup(r.text, 'html.parser')
xcsrf = soup.find("meta", {"name": "csrf-token"})["content"]